# Описание
В данном ноутбуке выполняется генерация дополнительных данных для категорий, содержащих недостаточное количество собственных образцов. Генерация осуществляется с использованием опенсорсной языковой модели T-lite. Полученные данные преобразуются в требуемый формат и добавляются к датасету.

# Import

In [ ]:
import pandas as pd
import numpy as np

import json
import re

import torch
from transformers import AutoModelForCausalLM, AutoTokenizer

from tqdm import tqdm

import pickle

import warnings
warnings.filterwarnings('ignore')

In [2]:
device = 'cuda' if torch.cuda.is_available() else 'cpu'
device

'cuda'

In [ ]:
model_name = 'MilyaShams/T-lite-it-1.0_Q4_0'

tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name,
                                             device_map='auto',
                                             torch_dtype='auto')

In [3]:
df = pd.read_parquet('full_df.parquet')
category_tree = pd.read_csv('category_tree.csv')

# Генерация данных с помощью LLM

In [7]:
str(category_tree[category_tree['cat_id'] == 1370]['cat_name'].values[0])

'Аккумуляторные батареи'

In [1]:
def gen(df: pd.DataFrame) -> dict:
    """
    Генерирует названия товаров для редких категорий из датафрейма.
    Для каждой категории с количеством примеров <= 50, отправляет запрос к языковой модели
    с просьбой сгенерировать 100 разнообразных товаров, относящихся к этой категории.
    
    :param df: DataFrame, содержащий колонку 'labels' с ID категорий.
    :return full_list: cловарь, где ключ — ID категории (cls), значение — строка с json-ответом от модели.
    """

    full_list = {}

    categories_to_generate = [
        (cls, value) for cls, value in df['labels'].value_counts().items()
        if value <= 50
    ]

    for cls, value in tqdm(categories_to_generate,
                           total=len(categories_to_generate),
                           desc='Генерация товаров'):
        messages = [
            {
                'role':
                'user',
                'content':
                f"Сгенерируй 100 похожих, но разнообразных товаров относящихся к категории: \
                {str(category_tree[category_tree['cat_id'] == cls]['cat_name'].values[0])}. \
                Генерируй только название. Ответ дай в формате json."
            },
        ]

        input_ids = tokenizer.apply_chat_template(messages,
                                                  add_generation_prompt=True,
                                                  return_tensors='pt').to(
                                                      model.device)

        outputs = model.generate(
            input_ids,
            max_new_tokens=10000,
        )

        full_list[cls] = tokenizer.decode(outputs[0], skip_special_tokens=True)

    return full_list

In [11]:
full_list = gen(df)

Генерация товаров:   0%|          | 0/430 [00:00<?, ?it/s]Генерация товаров: 100%|██████████| 430/430 [17:51:13<00:00, 149.47s/it]   


In [12]:
# сохраняем список конечных категорий
with open('full_list.pkl', 'wb') as file:
        pickle.dump(full_list, file)

In [13]:
full_list

{10652: 'user\nСгенерируй 100 похожих, но разнообразных товаров относящихся к категории: Кубики для малышей. Генерируй только название. Ответ дай в формате json.\nassistant\n```json\n[\n    "Кубики-пирамидки из натурального дерева",\n    "Кубики с буквами и цифрами для раннего обучения",\n    "Магнитные кубики с животными",\n    "Кубики с пазлами для развития мелкой моторики",\n    "Кубики с шумовыми элементами для тактильного восприятия",\n    "Кубики с цветными гранями для изучения цветов",\n    "Кубики-головоломки с вкладышами",\n    "Кубики-музыкальные инструменты с различными звуками",\n    "Кубики с магнитными буквами для создания слов",\n    "Кубики с развивающими заданиями на логику",\n    "Кубики-сортеры с различными формами",\n    "Кубики с яркими картинками для распознавания объектов",\n    "Кубики с магнитными стрелками для изучения направлений",\n    "Кубики с наклейками для творчества",\n    "Кубики с геометрическими фигурами для изучения форм",\n    "Кубики-пазлы с изобр

# Add generated

In [ ]:
def extract_names_from_json(text: str) -> list:
    """
    Извлекает JSON из текста с помощью регулярного выражения и получает список названий.
    
    :param text: строка, содержащая JSON в формате ```json\n...\n```.
    :return: список названий товаров или пустой список, если JSON не найден.
    """
    match = re.search(r'```json\n(.*?)\n```', text, re.DOTALL)

    if match:
        try:
            clean_json = match.group(1)  # получаем только JSON
            parsed_data = json.loads(clean_json)  # разбираем JSON
            return [item['name'] for item in parsed_data]  # извлекаем названия
        except json.JSONDecodeError:
            print('Ошибка при разборе JSON!')
            return []
    else:
        print('Не найден JSON в тексте!')
        return []

In [ ]:
def add_generated_data(df: pd.DataFrame, full_d: dict) -> pd.DataFrame:
    """
    Добавляет сгенерированные данные в DataFrame, заполняя отсутствующие колонки модой.
    
    :param df: исходный DataFrame (должен содержать колонки 'cat_id' и 'name').
    :param full_list: словарь, где ключ — cat_id, а значение — строка с JSON.
    :return: DataFrame с добавленными строками.
    """
    new_rows = []  # список для новых строк

    for cat_id, json_text in full_d.items():

        # определяем моду по категории
        mode_values = df[df['cat_id'] == cat_id].mode().iloc[0]

        names = extract_names_from_json(
            json_text)  # извлекаем названия товаров

        for name in names:
            new_row = {col: np.nan
                       for col in df.columns}  # создаем пустую строку с NaN
            new_row['cat_id'] = cat_id  # заполняем cat_id
            new_row['source_name_model'] = name  # заполняем name

            # заполняем остальные колонки модой категории
            for col in ['самовывоз', 'возможность доставки', 'гарантия']:
                new_row[
                    col] = mode_values[col] if col in mode_values else np.nan

            new_rows.append(new_row)

    # создаем DataFrame из новых строк
    new_df = pd.DataFrame(new_rows)

    # объединяем с существующим датафреймом
    df = pd.concat([df, new_df], ignore_index=True)

    return df

In [ ]:
full_df = add_generated_data(df, full_list)

In [ ]:
# сохраняем датасет в который добавили сгенерированные данные
full_df.to_parquet('full_df.parquet', index=False)